In [1]:
import os
import re
import json
import huggingface_hub

from tqdm import tqdm
from openai import OpenAI

from langchain.schema import Document

from dotenv import load_dotenv
load_dotenv("../keys.env")

openai_api_key = os.getenv('OPENAI_API_KEY')
os.environ['OPENAI_API_KEY'] = openai_api_key

hf_token = os.getenv("HF_TOKEN")
huggingface_hub.login(hf_token)

The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `huggingface-cli` if you want to set the git credential as well.
Token is valid (permission: read).
Your token has been saved to /home/pervinco/.cache/huggingface/token
Login successful


In [2]:
client = OpenAI()
model = "gpt-4o"

In [3]:
def load_jsonl(file_path):
    with open(file_path, 'r', encoding='utf-8') as f:
        return [json.loads(line) for line in f]

def load_document(path="../dataset/labeled_documents.jsonl"):
    raw_documents = load_jsonl(path)

    documents = []
    for doc in raw_documents:
        doc_id = doc['docid']
        content = doc['content']

        documents.append(Document(page_content=content, metadata={"docid": doc_id}))

    return documents

In [4]:
def clean_json_response(response):
    # 코드 블록(예: ```json, ```) 제거
    cleaned_response = re.sub(r'```(?:json)?', '', response).strip()
    return cleaned_response

def summarize_documents(document, model:str, client:OpenAI):
    prompt = (
        "당신은 한국어 문서를 읽고 핵심 내용을 요약하는 전문가입니다. "
        "주어진 한국어 문서를 읽고 가장 핵심이 되는 내용만 요약해서 한 줄의 문장으로 정리하세요. "
        "하지만 중요한 세부 사항을 생략하지 마세요. 특히 다음과 같은 사항들이 반드시 포함되어야 합니다: "
        "- 주요 등장인물 또는 대상"
        "- 그들의 행동이나 상태의 변화"
        "- 주요 사건이나 논의의 결과 또는 이유"
        "- 대화의 맥락 또는 논리적 전개 "
        "요약은 너무 일반적이지 않도록 하고, 핵심 내용이 드러나도록 하세요. "
        "반환하는 형식은 반드시 JSON 포맷이어야 하며, 모든 문자열은 쌍따옴표로 감싸야 합니다. "
        "형식은 다음과 같아야 합니다: "
        '{ "summarized_doc": "요약한 문서 내용" }. '
    )

    completion = client.chat.completions.create(
        model=model,
        messages=[
            {"role" : "system", "content" : prompt},
            {"role" : "user", "content" : document}
        ],
    )
    
    response = completion.choices[0].message.content
    response = clean_json_response(response)
    
    try:
        json_response = json.loads(response)
    except json.JSONDecodeError:
        return {"error": "Invalid JSON response", "response": response}
    
    if "summarized_doc" not in json_response:
        return {"error": "'summarized_doc' key not found", "response": response}
    
    return json_response


In [5]:
def process_documents(documents, model, client, output_path='../dataset/en_4.0_documents.jsonl'):
    with open(output_path, 'w', encoding='utf-8') as outfile:
        for idx, doc in enumerate(documents):
            print(f"{idx:04}")
            print(doc.metadata['docid'])

            doc_content = doc.page_content
            summarized = summarize_documents(doc_content, model, client)
            print(doc_content)
            
            if "summarized_doc" not in summarized:
                print(f"Error: 'summarized_doc' key not found for document {doc.metadata['docid']}")
                continue  # 오류가 발생한 문서는 스킵

            summarized_content = summarized["summarized_doc"]
            print(summarized_content, '\n')
                
            # 새로운 문서 구조
            result = {
                "docid": doc.metadata["docid"],
                "content": summarized_content,
                "doc_content" : doc_content
            }
                
            json.dump(result, outfile, ensure_ascii=False)
            outfile.write('\n')

In [6]:
documents = load_document(path="../dataset/labeled_documents.jsonl")

document = documents[997]
summarized_document = summarize_documents(document.page_content, model, client)

print("원본 문서:", document.page_content)
print("번역 문서:", summarized_document['summarized_doc'])

원본 문서: 셰기는 최근에 매장된 여성을 파내고 그녀와 성관계를 갖는 것에 대한 환상을 갖고 있습니다. 이러한 환상을 친구들에게 말했고, 그들은 그에게 치료를 받을 것을 권해주었습니다. 이 치료의 일환으로 셰기는 자신의 환상에 맞춰 자위를 하게 됩니다. 그리고 오르가즘 직전에는 살아있는 여성과 성관계를 가지는 환상으로 전환됩니다. 이러한 절차는 오르가즘 재조건화의 일부입니다.
번역 문서: 셰기는 매장된 여성과 성관계를 갖는 환상을 치료하기 위해 친구들의 권유로 오르가즘 재조건화 치료를 받으며, 환상에서 살아있는 여성과의 관계로 전환하는 과정을 거칩니다.


In [7]:
process_documents(documents, model, client, output_path="../dataset/summarized_documents.jsonl")

0000
42508ee0-c543-4338-878e-d98c6babee66
건강한 사람이 에너지 균형을 평형 상태로 유지하는 것은 중요합니다. 에너지 균형은 에너지 섭취와 에너지 소비의 수학적 동등성을 의미합니다. 일반적으로 건강한 사람은 1-2주의 기간 동안 에너지 균형을 달성합니다. 이 기간 동안에는 올바른 식단과 적절한 운동을 통해 에너지 섭취와 에너지 소비를 조절해야 합니다. 식단은 영양가 있는 식품을 포함하고, 적절한 칼로리를 섭취해야 합니다. 또한, 운동은 에너지 소비를 촉진시키고 근육을 강화시킵니다. 이렇게 에너지 균형을 유지하면 건강을 유지하고 비만이나 영양 실조와 같은 문제를 예방할 수 있습니다. 따라서 건강한 사람은 에너지 균형을 평형 상태로 유지하는 것이 중요하며, 이를 위해 1-2주의 기간 동안 식단과 운동을 조절해야 합니다.
건강한 사람이 에너지 균형을 1-2주 동안 유지하기 위해 영양가 있는 식단과 적절한 운동으로 에너지 섭취와 소비를 조절해야 함으로써 비만이나 영양 실조 예방이 가능하다. 

0001
4a437e7f-16c1-4c62-96b9-f173d44f4339
수소, 산소, 질소 가스의 혼합물에서 평균 속도가 가장 빠른 분자는 수소입니다. 수소 분자는 가장 가볍고 작은 원자로 구성되어 있기 때문에 다른 분자들보다 더 빠르게 움직입니다. 이러한 이유로 수소 분자는 주어진 온도에서 가장 빠른 평균 속도를 가지고 있습니다. 수소 분자는 화학 반응에서도 활발하게 참여하며, 수소 연료로도 널리 사용됩니다. 따라서 수소 분자는 주어진 온도에서 평균 속도가 가장 빠른 분자입니다.
수소, 산소, 질소 가스의 혼합물에서 수소 분자는 가장 가볍고 작은 원자로 구성되어 있어 주어진 온도에서 가장 빠른 평균 속도를 가지며, 화학 반응에 활발히 참여하고 연료로 많이 사용됩니다. 

0002
d3c68be5-9cb1-4d6e-ba18-5f81cf89affb
종이와 플라스틱은 재활용 가능한 자원입니다. 중학교 과학 수업에서 우리는 종이와 플라스틱 가방을 